# Normalizing Token Spelling

In handwritten documents, and particularly those in early modern Spanish, there is a wide range of spelling variation that will affect the representation of each token, and thus the performance of our model. Here, we provide a way to incorporate a dictionary that standardizes spelling through tokens' NORM attribute (as recommended by [Spacy creators](https://stackoverflow.com/questions/49493232/how-to-add-custom-slangs-into-spacys-norm-exceptions-py-module).

In [ ]:
#First, importn necessary modules

from spacy.lang.es import Spanish 
from spacy import displacy
import spacy
from spacy.tokens import Doc
from collections import defaultdict, Counter
from spacy.attrs import ORTH
import pandas as pd

In [75]:
# Load the large Spanish model
nlp = spacy.load('es_core_news_md')

In [80]:
#Read the text files to be processed
df = pd.read_csv('DocumentosTest.txt', delimiter =",")
print(df)

       id                                          document.
0       1   martin de gaynça maestro mayor de las obras d...
1       2   martin de gaynça  soy convenido  con los reve...
2       3   martin de gaynça  soy convenido  con el mones...
3       4   Francisco Buelta, cantero, vecino de Sevilla,...
4       5   Martin de Gainza y Juan de Escalona, vecinos ...
5       6   Martin de Gainza, se obligo a pagar a Juan Pe...
6       7   Rodrigo Alonso, calero, se obligo a pagar a M...
7       8   Fernan Rodriguez, cantero, vecino de Jerez de...
8       9   Ochoa de Isasi, maestro marmolero, y Martin d...
9      10   Martin de Gainza y Juan de Gainza, cantero, o...
10     11   Martin de Gainza, otorgo poder a Juanes de Ve...
11     12             Martin de Gainza. Escritura de deudo.]
12     13   Martin de Gainza, obrero mayor de la canteria...
13     14   Martin de Gainza, vizcaino, se constituyo en ...
14     15   Pedro Montañes, cantero, y Martin de Gainza, ...
15     16   Pedro Montañ

In [ ]:
# Read our normalization dictionary from JSON file
with open('normalizeddict.json', 'r', encoding='utf-8') as fp3:
    NORM_EXCEPTIONS = json.load(fp3)

Next, we define the function that updates the .norm attribute for each token, and add it to the pipeline as the first pipeline component (thus being applied after the parser, but before any other models)

In [ ]:
#Define and add pipeline component that updates .norm attribute

def add_custom_norms(doc):
    for token in doc:
        if token.text in NORM_EXCEPTIONS:
            token.norm_ = NORM_EXCEPTIONS[token.text]
    return doc

#Add component to the pipeline

nlp.add_pipe(add_custom_norms, first=True)

Then we run the pipeline on our set of texts:

In [81]:
docs=list(nlp.pipe(df['document.']))

And we can visualize the token texts and the normalized spellings to see how it was applied.

In [39]:
for doc in docs:
    for token in doc:
        print(token.text,token.norm_)

... ...
martin Martin
de de
gaynça Gainza
maestro maestro
mayor mayor
de de
las las
obras obras
de de
canteria canteria
de de
la la
santa santa
iglesia iglesia
de de
Sevilla sevilla
y y
juan Juan
sanchez Sanchez
de de
caliz Cadiz
maestro maestro
mayor mayor
de de
las las
obras obras
( (
roto roto
) )
desta de esta
dicha dicha
ciudad ciudad
de de
sevilla Sevilla
... ...
otorgamos otorgamos
... ...
que que
damos damos
todo todo
nuestro nuestro
poder poder
... ...
a a
rodrigo Rodrigo
de de
cordova Cordoba
vecino vecino
de de
la la
ciudad ciudad
de de
gibraltar Gibraltar
... ...
para para
... ...
que que
por por
nos nos
... ...
pueda pueda
fazer hacer
qualquier cualquier
yguala iguala
e y
convenencia convenencia
... ...
con con
luis Luis
de de
toro toro
en en
nombre nombre
de de
su su
majestad majestad
para para
fazer hacer
un un
muro muro
de de
abajo abajo
que que
se se
a a
de de
fazer hacer
en en
la la
ciudad ciudad
de de
gibraltar Gibraltar
desde desde
san san
francisco Francisco
fasta 

Caballeros caballeros
. .
] ]
   
Pedro pedro
Montañes montañes
, ,
cantero cantero
, ,
y y
Martin martin
de de
Gainza gainza
, ,
se se
obligaron obligaron
a a
traer traer
para para
la la
Catedral catedral
, ,
cuatrocientas cuatrocientas
carretadas carretadas
de de
piedra piedra
de de
las las
canteras canteras
de de
Moron moron
. .
] ]
   
Pedro pedro
Montañes montañes
, ,
cantero cantero
, ,
y y
Martin martin
de de
Gainza gainza
, ,
como como
su su
fiador fiador
, ,
se se
obligaron obligaron
a a
sacar sacar
para para
la la
Catedral catedral
, ,
quinientas quinientas
carretadas carretadas
de de
piedra piedra
de de
Moron moron
. .
] ]
   
Martin martin
de de
Gainza gainza
, ,
otorgo otorgo
poder poder
para para
cobrar cobrar
lo lo
adeudado adeudado
por por
Juan juan
de de
Ugarte ugarte
, ,
vizcaino vizcaino
, ,
estante estante
en en
Nueva nueva
España españa
. .
] ]
   
Isabel isabel
Nuñez nuñez
, ,
viuda viuda
de de
Martin martin
de de
Gainza gainza
y y
su su
heredera heredera
universa

   
Juan juan
de de
Santander santander
, ,
como como
principal principal
, ,
Juan juan
de de
Matencio matencio
y y
Diego diego
de de
Riaño riaño
, ,
canteros canteros
, ,
vecinos vecinos
de de
Sevilla sevilla
, ,
como como
fiadores fiadores
, ,
se se
obligaron obligaron
a a
pagar pagar
a a
Juan juan
de de
Escalante escalante
, ,
ocho ocho
mil mil
maravedis maravedis
. .
] ]
   
D. Don
de de
R. r.
, ,
cantero cantero
, ,
estante estante
en en
Sevilla sevilla
, ,
otorgo otorgo
poder poder
a a
Juan juan
de de
Escalante escalante
, ,
mercader mercader
, ,
para para
que que
hiciese hiciese
efectivos efectivos
sus sus
creditos creditos
. .
] ]
   
Se se
obligo obligo
a a
sacar sacar
en en
paz paz
y y
salvo salvo
al al
Cabildo cabildo
y y
Regimiento regimiento
de de
Sevilla sevilla
de de
los los
diez diez
mil mil
maravedis maravedis
en en
que que
se se
habia habia
concertado concertado
con con
ciertos ciertos
canteros canteros
, ,
vecinos vecinos
de de
Jerez jerez
de de
la la
Frontera fronte

Sigue sigue
la la
escritura escritura
con con
otras otras
condiciones condiciones
que que
hacen hacen
referencia referencia
a a
las las
circunstancias circunstancias
economicas economicas
y y
de de
personal personal
, ,
pero pero
sin sin
interes interes
para para
la la
tecnica tecnica
de de
la la
obra obra
] ]
. .
... ...
maestre maestre
Cristobal cristobal
albañi albañil
vecino vecino
de de
... ...
sevilla Sevilla
en en
la la
collacion collacion
de de
santa santa
maria Maria
madalena Magdalena
... ...
fago hago
pacto pacto
... ...
con con
vos vos
juan Juan
fernandes Fernandez
de de
castro Castro
vecino vecino
... ...
en en
la la
collacion collacion
de de
san san
salvador Salvador
... ...
de de
tal tal
manera manera
que que
... ...
me me
obligo obligo
de de
faser hacer
en en
una una
capilla capilla
que que
... ...
teneis teneis
y y
esta esta
en en
el el
monesterio monasterio
de de
san san
francisco Francisco
de de
esta esta
dicha dicha
ciudad ciudad
que que
es es
la la
primera primera


anbos ambos
a a
dos dos
de de
mancomun mancomun
... ...
hazemos hacemos
pabto pacto
... ...
con con
vos vos
gomez Gomez
garcia Garcia
clerigo clerigo
presbitero presbitero
... ...
en en
tal tal
manera manera
... ...
que que
nos nos
obligamos obligamos
de de
hazer hacer
en en
el el
ospital hospital
del del
rey rey
la la
obra obra
de de
albañeria albañeria
... ...

    
   
primeramente primeramente
que que
el el
maestro maestro
albañi albañil
que que
esta esta
obra obra
tomare tomare
derrueque derroque
dos dos
paredes paredes
de de
tres tres
tapias tapias
en en
largo largo
desde desde
la la
pared pared
nueva nueva
que que
sera sera
mostrada mostrada
col col
tejado tejado
que que
en en
toda toda
esta esta
longura longura
aparte aparte
todo todo
el el
ladrillo ladrillo
y y
lo lo
ponga ponga
en en
salvo salvo

    
   
yten item
que que
abra abra
tres tres
sanjas zanjas
en en
estas estas
dos dos
paredes paredes
de de
en en
una una
a a
otra otra
que que
son son
tres tres
estas estas
sanjas 

...

por por
mi mi
manufatura manufactura
e y
trabajo trabajo
cunplimento cumplimiento
a a
tres tres
reales reales
por por
cada cada
libra libra
de de
manera manera
que que
lo lo
que que
la la
dicha dicha
fabrica fabrica
me me
a a
de de
pagar pagar
por por
la la
dicha dicha
manifatura manufactura
e y
trauajo trabajo
a a
de de
ser ser
lo lo
que que
menos menos
le le
costare costare
a a
la la
dicha dicha
fabrica fabrica
de de
tres tres
reales reales
cada cada
libra libra
del del
dicho dicho
bronze bronce
hierro hierro
y y
estaño estaño
lo lo
qual cual
se se
me me
pague pague
de de
la la
manera manera
que que
de de
yuso yuso
sera sera
declarado declarado

    
   
... ...
asy asi
mesmo mismo
me me
a a
de de
pagar pagar
por por
la la
dicha dicha
manifatura manufactura
e y
trauajo trabajo
... ...
otros otros
quinientos quinientos
ducados ducados
muertos muertos

    
   
... ...
que que
se se
me me
a a
de de
dar dar
la la
pieça pieza
que que
al al
presente presente
esta esta
en en
el el
estudio 

de de
todos todos
los los
maravedis maravedis
que que
ove hube
de de
aver haber
e y
monto monto
la la
echura hechura
e y
manos manos
de de
la la
dicha dicha
çanefa cenefa
... ...
... ...
lazaro Lazaro
diaz Diaz
labrador labrador
vecino vecino
desta de esta
cibdad ciudad
de de
seuilla Sevilla
en en
la la
collacion collacion
de de
sant san
lloreynte Lorenzo
otorgo otorgo
... ...
que que
do do
e y
otorgo otorgo
... ...
poder poder
... ...
a a
vos vos
alonso Alonso
fernandes Fernandez
batihoja batihoja
... ...
especialmente especialmente
para para
que que
... ...
en en
mi mi
nonbre nombre
... ...
podades podades
demandar demandar
... ...
de de
juan Juan
de de
trugillo Trujillo
tonelero tonelero
mayordomo mayordomo
de de
la la
casa casa
de de
señor señor
sant san
Sebastian sebastian
del del
canpo campo
desta de esta
cibdad ciudad
de de
seuilla Sevilla
... ...
nueve nueve
mil mil
e y
setecientos setecientos
maravedis maravedis
... ...
que que
me me
deve debe
e y
es es
obligado obligado
a a
m

nuestro nuestro
poder poder
... ...
e y
los los
diez diez
mil mil
marauedis maravedis
restantes restantes
... ...
acabada acabada
de de
fazer hacer
... ...
de de
oy hoy
en en
diez diez
meses meses
... ...
[ [
Fiador fiador
, ,
Gaspar gaspar
de de
Lujan lujan
, ,
bordador bordador
, ,
vecino vecino
de de
Sevilla sevilla
. .
] ]
... ...
matheo Mateo
de de
leon leon
bordador bordador
vezino vecino
de de
seuilla Sevilla
en en
la la
collacion collacion
de de
santa santa
maria Maria
otorgo otorgo
e y
conosco conozco
que que
soy soy
convenido convenido
... ...
con con
vos vos
los los
... ...
señores señores
dean dean
e y
cabildo cabildo
de de
la la
santa santa
yglesia iglesia
desta de esta
cibdad ciudad
de de
seuilla Sevilla
... ...
en en
tal tal
manera manera
que que
yo yo
sea sea
obligado obligado
... ...
de de
faser hacer
( (
roto roto
) )
xabastros jabastros
del del
terno terno
verde verde
nuebo nuevo
de de
la la
dicha dicha
santa santa
yglesia iglesia
conforme conforme
a a
los los
faldon

esta esta
obra obra
an han
de de
dar dar
el el
terciopelo terciopelo
sobre sobre
que que
se se
a a
de de
bordar bordar
y y
el el
oficial oficial
que que
lo lo
hubiere hubiere
de de
hazer hacer
a a
de de
poner poner
toda toda
la la
costa costa
que que
lleuare llevare
de de
oro oro
y y
sedas sedas
con con
las las
demas demas
costas costas
si si
no no
fuere fuere
aforro aforo
y y
guarniciones guarniciones
y y
guarnezel guarnezel
de de
que que
es es
a a
costa costa
del del
señor señor
de de
la la
obra obra
este este
debuxo dibujo
ha ha
de de
ser ser
con con
las las
mismas mismas
condiciones condiciones
del del
otro otro
el el
cordero cordero
ha ha
de de
ser ser
de de
plata plata
y y
sedas sedas
pardas pardas
de de
borianado borianado
y y
el el
rostro rostro
y y
pies pies
y y
manos manos
de de
punraje punraje
plata plata
debaxo debajo
del del
tenido tenido
el el
libro libro
de de
oro oro
llano llano
y y
la la
bandera bandera
los los
retulos rotulos
de de
plata plata
llana llana
entiendese e

al al
romano romano
y y
el el
bordado bordado
de de
vn un
cuerpo cuerpo
de de
capa capa
de de
carmesi carmesi
y y
para para
en en
cuenta cuenta
tenia tenia
recibido recibido
51829 51829
maravedis maravedis
y y
el el
dicho dicho
pedro Pedro
de de
santisteban Santiesteban
es es
fallecido fallecido
... ...
[ [
el el
se se
encarga encarga
de de
proseguirla proseguirla
en en
las las
condiciones condiciones
que que
el el
citado citado
Santisteban Santiesteban
las las
tenia tenia
. .
El el
documento documento
esta esta
muy muy
deteriorado deteriorado
y y
por por
ello ello
no no
se se
transcriben transcriben
las las
formulas formulas
siguientes siguientes
. .
] ]
... ...
cosme cosme
de de
caravajal Carvajal
bordador bordador
... ...
e y
yo yo
pedro Pedro
de de
padilla Padilla
bordador bordador
... ...
como como
principales principales
obligados obligados
e y
yo yo
luis Luis
de de
abreu Abreu
escriptor escritor
de de
libros libros
... ...
como como
su su
fiador fiador
... ...
otorgamos otorgamo

In [66]:
for doc in docs:
    for token in doc:
        print(token.norm_,end=" ")
    print("\n\n")

... Martin de Gainza maestro mayor de las obras de canteria de la santa iglesia de sevilla y Juan Sanchez de Cadiz maestro mayor de las obras ( roto ) de esta dicha ciudad de Sevilla ... otorgamos ... que damos todo nuestro poder ... a Rodrigo de Cordoba vecino de la ciudad de Gibraltar ... para ... que por nos ... pueda hacer cualquier iguala y convenencia ... con Luis de toro en nombre de su majestad para hacer un muro de abajo que se a de hacer en la ciudad de Gibraltar desde san Francisco hasta encima del cuchillo de una sierra que a de ser el dicho muro de grueso de nueve pies desde el dicho monasterio de san Francisco hasta la cueva de san Cristobal y desde la dicha cueva ... hasta el cuchillo de la sierra a de ser de cuatro pies de grueso ... y otrosi nos pueda obligar que haremos otras cualesquier obras de canteria y mamposteria que fueren menester de se hacer en la dicha ciudad de gibraltar 


... Martin de Gainza ... soy convenido ... con los reverendos padres prior frailes y

  emancipacion de un hijo de juan lorenzo , mercader de libros , cuya escritura fue otorgada en casa de diego de riaño , maestro mayor de las obras de la santa iglesia de sevilla . ] 


  otorgo poder a juan picardo , cantero , para que cobrase a pedro portugues , cantero , cinco ducados de oro ; a juan de murga , albañil , siete ducados de oro y a cristobal gonzalez , ballestero , tres ducados y medio de oro que le adeudaban . ] 


  juan de escalante , mercader , procurador principal de diego de riaño , designa procuradores sustitutos de este a juan picardo y a martin de gainza , canteros . ] 


  otorgo poder a martin de otamendi , cantero , estante en sevilla , para que cobrase a alonso perez de la bolsa , mayordomo de la iglesia mayor de aracena , diez y ocho mil maravedis , importe del salario de tres años que dicha iglesia le daba por su cargo de las obras de canteria de ella . ] 


  recibio por aprendiz durante año y medio a pedro de veranga montañes , hijo de alonso veranga ,

... cristobal Garcia albañil ... y cristobal Garcia cantero ... nos ambos a dos de mancomun ... hacemos pacto ... con vos Gomez Garcia clerigo presbitero ... en tal manera ... que nos obligamos de hacer en el hospital del rey la obra de albañeria .... 
    primeramente que el maestro albañil que esta obra tomare derroque dos paredes de tres tapias en largo desde la pared nueva que sera mostrada col tejado que en toda esta longura aparte todo el ladrillo y lo ponga en salvo . 
    item que abra tres zanjas en estas dos paredes de en una a otra que son tres estas zanjas las ahonde ocho palmos y de seis palmos en ancho que las torne a zanjar los siete palmos de su cal y tierra y ripio segun pertenece a buena obra . 
    item que encima de estas dichas zanjas forme a sus cepas de albañeria de dos ladrillos de gordura y de tres tablados en alto encima de estas dichas cepas conforme a su cimiento en todo lo susodicho ladrillo y medio de gordura y dejando un cuarteron de cada parte de la sepa

    con todas estas condiciones se concerto esta obra con sebastian Garcia albañil el cual la a de dar acabada en el mas breve tiempo que ser pudiere andando por lo menos en ella dos maestros y dos aprendices con los peones necesario y a de ser obligado a traer mas todos los que le mandaren y el dia que por su culpa cesare la obra pierda cuatro ducados y se traigan oficiales a su costa y afianzada la dicha obra quede la paga de ella o el orden de la dicha paga a la disposicion de nuestro padre presidente y por la dicha obra se le a de dar novecientos ducados pagados por semanas fray Pedro de los angeles ( rubricado ) sebastian Garcia ( rubricado ) . 
    [ testigos de conocimiento : mateo de vergara y juan de ojeda , albañiles , vecinos de sevilla ] . 


... Juan Marin albañil vecino de sevilla en la collacion de san Roman otorgo que soy convenido ... con el señor Don Baltasar del rio obispo de escalas canonizo en la santa iglesia de Sevilla ... en tal manera que yo sea ... obligado ..

    item dende esta canal maestra teje todo este refectorio a tercio y pulgada conforme a buena obra con tierra y barro y la canal maestra quede de seis dedos de ancho a hilo y a regla muy bien encaxcada y envestida y revocada y como fuere haciendo y tejando el tejado por sus tronos va jhendo ? el caballete de tejas con su cal y arena y barro y encima lo encale de cal blanca y arista marmolado y por la banda de afuera ha de echar una cenefa encalada y a cordel y encale el desvan que va por la banda de fuera de dos manos con una cinta que ha de haber de dos palmos mas bajo del y la una mano de cal y arena y barro y arista y otra de cal blanca y arista que vaya bien bruñido y aguardado y como fuere tejando el tejado ha de ir haciendo caballete y cintas porque no buelva despues de tejado el tejado a lo hacer porque es perjuicio por manera que el dia que se acabare el tejado se concluyan los encalados de caballete y lo suso dicho . 
    item en el sobre caustro despues de puestos los basti

...

    item me obligo de poner sobre este dicho friso una orden de pilares segun y como estan señalados en la muestra de pergamino y de la misma altura y del grueso que al señor chantre pareciere los cuales asi altos como bajos han de ir ( roto ) tad unos de otros ( roto ) de hueco de pilar a pilar en el cual dicho friso y en la segunda orden del tengo ( roto ) y asentar cinco pilares con sus hojas muy bien sacadas limados y estañados los cuales han de ser conforme a los ( roto ) que estan señalados en la muestra de papel en la segunda orden de ella lo cual todo hare a contento de vos el dicho señor chantre . 
    item me obligo que sobre estos dichos pilares de esta segunda orden y sobre los demas que en ella han de ir hare otro friso de mi propia mano conforme a la ordenanza y muestra que en unos papeles esta dibujado ? ... todo lo relevado de estos dichos frisos y ( roto ) ordenanza de peones que esta en la muestra y ( roto ) dicho los cuales han de ir macizos y muy bien limados y cinz

    item en el ultimo vaso del dicho candelabro en el labrio de el lleve unas puntas agudas distantes dos de dos una de otra y otros dos de dos en alto las cuales seran del dicho metal o de hierro para que las aves no se puedan sentar alrededor del dicho baso todo lo dicho se entiende que a de llevar sus fuerzas bastante para que pueda perpetuarse sin hacer falta algun intorsimiento y en cuanto a la fortificacion de los dichos remates yo satisfaga a vos el dicho señor canonigo y al dicho maestro mayor y tome vuestro parecer y consejo . 
    item que cada uno de estos remates a de venir ? y lo tengo de dar hecho y darlo todo entero hecho todo una pieza de diversas piezas tan fuerte como si fuere de sola una pieza y los de todos los dichos remates repartidos limpios y pulidos y bien acabados a contento del dicho maestro mayor porque si alguna cosa se dorare de ellos halle ? el oro el asiento igual . 
    item que yo ponga todo el metal y hierro que fuere menester para los dichos cuatro a

    item que la dicha fabrica me de todo el bronce y hierro y estaño que fuere menester para hacer la dicha reja y sacando lo que a la dicha fabrica le costare cada libra del dicho bronce hierro y estaño sobre ello me a de dar y pagar la dicha fabrica por mi manufactura y trabajo cumplimiento a tres reales por cada libra de manera que lo que la dicha fabrica me a de pagar por la dicha manufactura y trabajo a de ser lo que menos le costare a la dicha fabrica de tres reales cada libra del dicho bronce hierro y estaño lo cual se me pague de la manera que de yuso sera declarado . 
    ... asi mismo me a de pagar por la dicha manufactura y trabajo ... otros quinientos ducados muertos . 
    ... que se me a de dar la pieza que al presente esta en el estudio de san Miguel de esta ciudad por traza y obrador de los pintores con el corral que esta junto a el o la parte que del me fuere señalado ... en el cual dicho corral se me han de dar fechas ... dos fraguas en cuanto toca al albañeria y pila

... Pedro de Bonilla y yo Mateo de leon bordadores vecinos de esta ciudad de Sevilla nos ambos a dos de mancomun ... otorgamos ... que somos convenidos ... con vos los ... señores dean y cabildo de la santa iglesia de Sevilla ... que nosotros nos obligamos y encargamos de hacer para la dicha fabrica cuatro faldones con cuatro mangas para el terno verde de la dicha santa iglesia ... que no lleve ningun enbutido conforme a las muestras ... a de montar toda la obra de ellos cuarenta mil maravedis cinco mil maravedis mas o menos ... los cuales ... pagueis ... treinta mil maravedis luego los cuales tenemos en nuestro poder ... y los diez mil maravedis restantes ... acabada de hacer ... de hoy en diez meses ... [ fiador , gaspar de lujan , bordador , vecino de sevilla . ] 


... Mateo de leon bordador vecino de Sevilla en la collacion de santa Maria otorgo y conozco que soy convenido ... con vos los ... señores dean y cabildo de la santa iglesia de esta ciudad de Sevilla ... en tal manera qu

... Pedro de las cuevas bordador vecino ... en la collacion de san Vicente otorgo ... que soy convenido ... con la fabrica de la iglesia de señor san Pedro de esta ciudad de Sevilla ... en tal manera que yo sea obligado ... de hacer y adobar unas cenefas y dalmaticas para la dicha iglesia ... conforme a las condiciones siguientes . 
    primeramente las cenefas de la casulla en el entorchado gordo de las retochas se a de rehenchir todos de nuevo porque lo demas de las retochas esta bueno y no es menester llegar a helo reparar los encasamentos que es rehenchirlos de las sedas que les faltan y las imagenes los cuales convenga a buen reparo y las encarnaciones de los rostros y de Cristo rehechirlas lo que esta saltado y abrirlas lo que fuere de menester y reparar todo el oro que estuviere levantado al fin que se repare todo lo que mas fuere de necesidad que no haya falta en ello . 
    los cuatro faldones y bocas de mangas otras cuatro es de menester entretallarlo y asentarlo sobre tercio

This pipeline component can be added prior to training to modify the performance of the model. As can be seen in our Evaluation notebooks, this leads to a slight improvement in performance.